In [1]:
import pandas as pd
import seaborn as sns
import numpy as np
%matplotlib inline
from matplotlib import pyplot as plt
import math
import psycopg2 as psy
from sqlalchemy import create_engine
from sqlalchemy.engine.url import URL

### Raw Data Source:

Raw data obtained from the National Youth in Transition Database (NYTD). See README for more information on sources.

##### Starting raw data sets:

###### A) Services and demographic data for Fiscal Years (FY) 2011 - 2014 (Baseline populations for each FY)
        
- Cross-sectional data collected over 8 six-month-periods

- For all foster youth receiving independent living services funded through CFCIP for each fiscal year

- Data collected from all 50 states (my data excludes data from Connecticut) and D.C. and Puerto Rico

- Total of 675645 rows, and 31 columns
        
###### B) Outcomes data for Wave 1 and Wave 2 of Cohort 1
            
- Cohort 1 consists of foster youth who received services in FY 2011 AND participated in surveys

- Longitudinal data collected, 2 follow-up periods (every 2 years)

- About 5% of baseline population (Dataset A, FY 2011)

- Wave 1 = Outcomes Survey collected in FY 2011, within 45 days of youth's 17th birthday, from 49 states and D.C. and Puerto Rico (data excludes data from Connecticut) 

- Wave 2 = Outcomes Follow-Up Survey collected in FY 2013, within 45 days of youth's 19th birthday, from 48 states and D.C. (data excludes data from Connecticut, New York and Puerto Rico)

- Missing: Wave 3 = Outcomes Follow-Up Survey collected in FY 2015, within 45 days of youth's 21st birthday

- Total of 22811 rows, and 48 columns
        
###### C) Outcomes data for Wave 1 of Cohort 2
            
- Cohort 2 consists of foster youth who received services in FY 2014 AND participated in surveys

- Longitudinal data collected, 2 follow-up periods (every 2 years)

- About 5% of baseline population (Dataset A, FY 2014)

- Data collected from 49 states and D.C. and Puerto Rico (data excludes data from Connecticut) 

- Wave 1 = Outcomes Survey collected in FY 2014, within 45 days of youth's 17th birthday

- Missing: Wave 2 = Outcomes Follow-Up Survey to be collected in FY 2016, within 45 days of youth's 21st birthday

- Missing: Wave 3 = Outcomes Follow-Up Survey to be collected in FY 2018, within 45 days of youth's 21st birthday

- Total of 23775 rows, and 49 columns

__________________________________________________________________________________________
### Data Cleaning and Munging Plan:
    
1) Load 3 starting datasets () into pandas dataframe for each

- As described in cell above: Dataset A, Dataset B, Dataset C

2) Create dataframe for Cohort 1 -- Baseline Population Dataset:

- Services and demographic data for foster youth in FY 2011 from dataset A 

- Outcomes data for Wave 1 Participants from dataset B

- Initial Data Review (look at tables, dtypes, etc.)

- Clean data:
    
    - Unfortunately, several states have badly encoded unique ID values, which prevents me from tracking those 
      records. Need to drop data rows from the following states due to data quality issue:
      ["HI", "IN", "KY", "MS", "OR", "TX", "TN"]
      
    - Remove duplicates (based on unique IDs)
    
    - Missing Data?
        
    - Save dataset as CSV file and as table in local postgreSQL database
    
3) Create dataframe for Cohort 1 -- Wave 2 Outcomes Dataset:

- Outcomes data for Wave 2 Participants from dataset B

- Only include foster youth who completed surveys in Wave 2

- Clean data:

    - Drop rows that have missing values in multiple columns (>10)

    - Convert data type of columns AgeMP, EduLevlSv, RaceDcl, RaceUnkn to int

    - Convert data types of columns RepDates_outcomes, RepDates_services and DOB to datetime

    - Identify categorical variable columns that may need to be dummified for later analysis

    - Get rid of special characters (that are not UTF-8) in column HighEdCert
    
    - Remove duplicates (based on unique IDs)

- Load cleaned dataset into local postgres DB

3) Create dataframe for Cohort 2 -- Baseline Population Dataset:

- Services and demographic data for foster youth in FY 2014 from dataset A

- Initial Data Review (look at tables, dtypes, etc.)

- Clean data:
    
    - Convert data type of columns AgeMP, EduLevlSv, RaceDcl, RaceUnkn to int

    - Convert data types of columns RepDates_outcomes, RepDates_services, outcmdte and DOB to datetime

    - Identify categorical variable columns that may need to be dummified for later analysis

    - Unfortunately, several states have badly encoded unique ID values, which prevents me from tracking those 
      records. Need to drop data rows from the following states due to data quality issue:
      ["HI", "IN", "KY", "MS", "OR", "TX", "TN"]

- Load cleaned dataset into local postgres DB

# START Data Clean and Munge

In [3]:
# Load 3 initial datasets into pandas DF

In [4]:
services_11_14 = pd.read_csv('~/Desktop/dsi_projects_backup/capstone/data_to_use/raw/Services_2014.csv')

/Users/cguy/anaconda/lib/python2.7/site-packages/IPython/core/interactiveshell.py:2723: DtypeWarning: Columns (12,13,19,38) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [5]:
outcomes_2013 = pd.read_stata('~/Desktop/dsi_projects_backup/capstone/data_to_use/raw/Outcomes2011Wave2_.dta')

In [6]:
outcomes_2014 = pd.read_stata('~/Desktop/dsi_projects_backup/capstone/data_to_use/raw/Outcomes14_W1.dta')

In [7]:
list(services_11_14)

['FY',
 'RepDate',
 'StFIPS',
 'St',
 'RecNumbr',
 'DOB',
 'Sex',
 'AmIAKN',
 'Asian',
 'BlkAfrAm',
 'HawaiiPI',
 'White',
 'RaceUnkn',
 'RaceDcln',
 'HisOrgin',
 'FCStatSv',
 'LclFIPSsv',
 'TribeSv',
 'DelinqntSv',
 'EdLevlSv',
 'SpecEdSv',
 'ILNAsv',
 'AcSuppSv',
 'PSEdSuppSv',
 'CareerSv',
 'EmplyTrSv',
 'BudgetSv',
 'HousEdSv',
 'HlthEdSv',
 'FamSuppSv',
 'MentorSv',
 'SILsv',
 'RmBrdFASv',
 'EducFinaSv',
 'OthrFinaSv',
 'StFCID',
 'Race',
 'RaceEthn',
 'AgeMP']

In [11]:
services_11_14.describe()

FY        RepDate         StFIPS            Sex  \
count  675645.000000  675645.000000  675645.000000  675645.000000   
mean     2012.462685  201252.261118      26.395412       1.516631   
std         1.113240     111.310146      16.358375       0.499724   
min      2011.000000  201103.000000       1.000000       1.000000   
25%      2011.000000  201109.000000      12.000000       1.000000   
50%      2012.000000  201209.000000      25.000000       2.000000   
75%      2013.000000  201309.000000      39.000000       2.000000   
max      2014.000000  201409.000000      72.000000       2.000000   

              AmIAKN          Asian       BlkAfrAm       HawaiiPI  \
count  675645.000000  675645.000000  675645.000000  675645.000000   
mean        0.036691       0.020037       0.368907       0.011923   
std         0.617899       0.605054       0.761098       0.598528   
min         0.000000       0.000000       0.000000       0.000000   
25%         0.000000       0.000000       0.000000       0.000000   
50%         0.000000       0.000000       0.000000       0.000000   
75%         0.000000       0.000000       1.000000       0.000000   
max        77.000000      77.000000      77.000000      77.000000   

               White       HisOrgin      ...             HousEdSv  \
count  675645.000000  675645.000000      ...        675645.000000   
mean        0.548146       0.318765      ...             8.897445   
std         0.770803       1.419459      ...            24.123840   
min         0.000000       0.000000      ...             0.000000   
25%         0.000000       0.000000      ...             0.000000   
50%         1.000000       0.000000      ...             0.000000   
75%         1.000000       0.000000      ...             1.000000   
max        77.000000      77.000000      ...            77.000000   

            HlthEdSv      FamSuppSv       MentorSv          SILsv  \
count  675645.000000  675645.000000  675645.000000  675645.000000   
mean        8.878888       8.827611       8.738966       8.663393   
std        24.129933      24.148215      24.181827      24.200287   
min         0.000000       0.000000       0.000000       0.000000   
25%         0.000000       0.000000       0.000000       0.000000   
50%         0.000000       0.000000       0.000000       0.000000   
75%         1.000000       1.000000       1.000000       0.000000   
max        77.000000      77.000000      77.000000      77.000000   

           RmBrdFASv     EducFinaSv     OthrFinaSv           Race  \
count  675645.000000  675645.000000  675645.000000  675645.000000   
mean        8.696876       8.750952       8.793846       9.967709   
std        24.194873      24.176128      24.167719      27.141931   
min         0.000000       0.000000       0.000000       1.000000   
25%         0.000000       0.000000       0.000000       1.000000   
50%         0.000000       0.000000       0.000000       1.000000   
75%         0.000000       1.000000       1.000000       2.000000   
max        77.000000      77.000000      77.000000      99.000000   

            RaceEthn  
count  675645.000000  
mean        5.345485  
std        15.597203  
min         1.000000  
25%         1.000000  
50%         2.000000  
75%         6.000000  
max        99.000000  

[8 rows x 31 columns]

In [8]:
list(outcomes_2013)

['Wave',
 'StChID',
 'StFIPS',
 'St',
 'RecNumbr',
 'RepDate',
 'dob',
 'Sex',
 'AmIAKN',
 'Asian',
 'BlkAfrAm',
 'HawaiiPI',
 'White',
 'RaceUnkn',
 'RaceDcln',
 'HisOrgin',
 'OutcmRpt',
 'OutcmDte',
 'OutcmFCS',
 'CurrFTE',
 'CurrPTE',
 'EmplySklls',
 'SocSecrty',
 'EducAid',
 'PubFinAs',
 'PubFoodAs',
 'PubHousAs',
 'OthrFinAs',
 'HighEdCert',
 'CurrenRoll',
 'CnctAdult',
 'Homeless',
 'SubAbuse',
 'Incarc',
 'Children',
 'Marriage',
 'Medicaid',
 'OthrHlthIn',
 'MedicalIn',
 'MentlHlthIn',
 'PrescripIn',
 'SampleState',
 'InSample',
 'Baseline',
 'FY11Cohort',
 'Elig19',
 'Weight',
 'Responded']

In [12]:
outcomes_2013.describe()

/Users/cguy/anaconda/lib/python2.7/site-packages/numpy/lib/function_base.py:3823: RuntimeWarning: Invalid value encountered in percentile
  RuntimeWarning)


Weight
count  22811.000000
mean       2.505278
std        2.241763
min        0.700000
25%             NaN
50%             NaN
75%             NaN
max       80.710000

In [13]:
list(outcomes_2014)

['wave',
 'stfips',
 'st',
 'recnumbr',
 'repdate',
 'dob',
 'sex',
 'amiakn',
 'asian',
 'blkafram',
 'hawaiipi',
 'white',
 'raceunkn',
 'racedcln',
 'hisorgin',
 'outcmrpt',
 'outcmdte',
 'outcmfcs',
 'currfte',
 'currpte',
 'emplysklls',
 'socsecrty',
 'educaid',
 'pubfinas',
 'pubfoodas',
 'pubhousas',
 'othrfinas',
 'highedcert',
 'currenroll',
 'cnctadult',
 'homeless',
 'subabuse',
 'incarc',
 'children',
 'marriage',
 'medicaid',
 'othrhlthin',
 'medicalin',
 'mentlhlthin',
 'prescripin',
 'baseline',
 'fy14cohort',
 'elig19',
 'samplestate',
 'insample',
 'responded',
 'race',
 'raceethn',
 'stfcid']

In [14]:
outcomes_2014.describe()

stfips     responded
count  23775.000000  23775.000000
mean      26.338212      0.733460
std       16.927417      0.442159
min        1.000000      0.000000
25%        9.000000      0.000000
50%       25.000000      1.000000
75%       40.000000      1.000000
max       72.000000      1.000000

In [22]:
# First I will create a data set that has services and demographic data (from 2011) for cohort 1 baseline population

In [104]:
# For cohort 1, only need services data for FY 2011
cohort_1 = services_11_14[services_11_14.FY == 2011]

# Dropping columns that are not needed for this project
cohort_1 = cohort_1.drop(['RecNumbr','LclFIPSsv'],axis= 1)

cohort_1.describe()

FY        RepDate         StFIPS            Sex         AmIAKN  \
count  173184.0  173184.000000  173184.000000  173184.000000  173184.000000   
mean     2011.0  201106.089974      26.569672       1.519696       0.030886   
std         0.0       2.998659      16.210084       0.499613       0.173010   
min      2011.0  201103.000000       1.000000       1.000000       0.000000   
25%      2011.0  201103.000000      12.000000       1.000000       0.000000   
50%      2011.0  201109.000000      25.000000       2.000000       0.000000   
75%      2011.0  201109.000000      36.000000       2.000000       0.000000   
max      2011.0  201109.000000      72.000000       2.000000       1.000000   

               Asian       BlkAfrAm       HawaiiPI          White  \
count  173184.000000  173184.000000  173184.000000  173184.000000   
mean        0.014118       0.373782       0.006317       0.531926   
std         0.117978       0.483808       0.079228       0.498981   
min         0.000000       0.000000       0.000000       0.000000   
25%         0.000000       0.000000       0.000000       0.000000   
50%         0.000000       0.000000       0.000000       1.000000   
75%         0.000000       1.000000       0.000000       1.000000   
max         1.000000       1.000000       1.000000       1.000000   

            HisOrgin      ...             HousEdSv       HlthEdSv  \
count  173184.000000      ...        173184.000000  173184.000000   
mean        0.292885      ...            14.481690      14.470448   
std         0.637311      ...            29.737938      29.743221   
min         0.000000      ...             0.000000       0.000000   
25%         0.000000      ...             0.000000       0.000000   
50%         0.000000      ...             0.000000       0.000000   
75%         0.000000      ...             1.000000       1.000000   
max         3.000000      ...            77.000000      77.000000   

           FamSuppSv       MentorSv          SILsv      RmBrdFASv  \
count  173184.000000  173184.000000  173184.000000  173184.000000   
mean       14.425882      14.342358      14.283796      14.309959   
std        29.764113      29.814385      29.836409      29.824874   
min         0.000000       0.000000       0.000000       0.000000   
25%         0.000000       0.000000       0.000000       0.000000   
50%         0.000000       0.000000       0.000000       0.000000   
75%         1.000000       1.000000       1.000000       1.000000   
max        77.000000      77.000000      77.000000      77.000000   

          EducFinaSv     OthrFinaSv          Race       RaceEthn  
count  173184.000000  173184.000000  173184.00000  173184.000000  
mean       14.370282      14.401954       9.74698       5.642167  
std        29.796868      29.798552      26.86216      16.506973  
min         0.000000       0.000000       1.00000       1.000000  
25%         0.000000       0.000000       1.00000       1.000000  
50%         0.000000       0.000000       2.00000       2.000000  
75%         1.000000       1.000000       2.00000       6.000000  
max        77.000000      77.000000      99.00000      99.000000  

[8 rows x 30 columns]

In [105]:
# Checking to see if unique IDs are repeated. Then need to determine if repeat is just a duplicate or means something

ID_count = dict(cohort_1.StFCID.value_counts())
set(cohort_1.StFCID.value_counts())

{1, 2}

In [106]:
duplicate_count = pd.DataFrame.from_dict(ID_count, orient='index')
duplicate_count[0].value_counts()

2    59411
1    54362
Name: 0, dtype: int64

Based on the information above: 
    
    - There are 113,773 total rows of data.
    
    - Of that total, 59,411 -- 52% -- are repeated

______________________________________________________________________
In the next two cells, I am checking the counts of duplicates in two different ways by utilizing 
the kwarg 'keep' in the 'DF.duplicated' class. For more information, see the documentation: 
http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.duplicated.html


In [107]:
dup_check_dict = dict(cohort_1.duplicated(['StFCID'],keep=False))

dup_count2 = pd.DataFrame.from_dict(dup_check_dict, orient='index')
dup_count2[0].value_counts()

True     118822
False     54362
Name: 0, dtype: int64

In [108]:
dup_check_dict = dict(cohort_1.duplicated(['StFCID'],keep='first'))

dup_count2 = pd.DataFrame.from_dict(dup_check_dict, orient='index')
dup_count2[0].value_counts()

False    113773
True      59411
Name: 0, dtype: int64

In [126]:
# Adding a new boolean column to baseline population dataframe that will 
# identify a duplicated order line item based on unique ID (False=Not a duplicate; True=Duplicate).
# Then sorting values based on Unique ID and RepDate columns

cohort_1['duplicated'] = cohort_1.duplicated(['StFCID'], keep=False)
cohort_1_dups = cohort_1[cohort_1['duplicated'] == True]
cohort_1_dups = cohort_1_dups.sort_values(['StFCID', 'RepDate'], ascending=[True, True])


In [131]:
# So, after examining resulting tables from cell above, I determined that the repeats are 
# those youth who were reported in both reporting periods for FY 2011 (RepDate: 201103 or 201109).
# Some repeats are duplicates of each other (containing the same information in both rows), 
# while some repeats need to be reviewed further.

# First, I will separate the repeats that are duplicates, drop one of the two rows for every unique ID, and merge 
# the remaining data rows with the non-duplicated data from cohort_1.

cohort_1_dups_b = cohort_1_dups.drop(['RepDate', 'AgeMP'], axis=1)

cohort_1_dups['duplicated_4_sure'] = cohort_1_dups_b.duplicated(keep=False)
cohort_1_dups.duplicated_4_sure.value_counts()


False    93602
True     25220
Name: duplicated_4_sure, dtype: int64

In [133]:
cohort_1_dups_2bAdded = cohort_1_dups[cohort_1_dups['duplicated_4_sure'] == True]
cohort_1_dups_2bAdded = cohort_1_dups_2bAdded.drop_duplicates('StFCID')
cohort_1_dups_2bAdded.duplicated_4_sure.value_counts()


True    12610
Name: duplicated_4_sure, dtype: int64

In [136]:
# Merging remaining data rows that are now unique and 
# adding to new dataframe with other data rows that were already unique...

cohort_1_NoDups = cohort_1[cohort_1['duplicated'] == False]
cohort_1_NoDups['duplicated'].value_counts()

False    54362
Name: duplicated, dtype: int64

In [137]:
cohort_1_dups_2bAdded = cohort_1_dups_2bAdded.drop(['duplicated','duplicated_4_sure'], axis=1)
cohort_1_NoDups = cohort_1_NoDups.drop('duplicated',axis=1)

frames = [cohort_1_dups_2bAdded, cohort_1_NoDups]

cohort_1_NoDups = pd.concat(frames)
cohort_1_NoDups.describe()

FY        RepDate        StFIPS           Sex        AmIAKN  \
count  66972.0   66972.000000  66972.000000  66972.000000  66972.000000   
mean    2011.0  201105.667801     25.980216      1.504823      0.030684   
std        0.0       2.981573     15.436015      0.499980      0.172463   
min     2011.0  201103.000000      1.000000      1.000000      0.000000   
25%     2011.0  201103.000000     12.000000      1.000000      0.000000   
50%     2011.0  201103.000000     27.000000      2.000000      0.000000   
75%     2011.0  201109.000000     36.000000      2.000000      0.000000   
max     2011.0  201109.000000     72.000000      2.000000      1.000000   

              Asian      BlkAfrAm      HawaiiPI         White      HisOrgin  \
count  66972.000000  66972.000000  66972.000000  66972.000000  66972.000000   
mean       0.013767      0.375231      0.006555      0.513976      0.300230   
std        0.116523      0.484186      0.080698      0.499808      0.651068   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.000000      0.000000      0.000000      0.000000   
50%        0.000000      0.000000      0.000000      1.000000      0.000000   
75%        0.000000      1.000000      0.000000      1.000000      0.000000   
max        1.000000      1.000000      1.000000      1.000000      3.000000   

           ...           HousEdSv      HlthEdSv     FamSuppSv      MentorSv  \
count      ...       66972.000000  66972.000000  66972.000000  66972.000000   
mean       ...          18.860628     18.860793     18.817670     18.749895   
std        ...          32.871587     32.871495     32.895545     32.933194   
min        ...           0.000000      0.000000      0.000000      0.000000   
25%        ...           0.000000      0.000000      0.000000      0.000000   
50%        ...           0.000000      0.000000      0.000000      0.000000   
75%        ...           1.000000      1.000000      1.000000      1.000000   
max        ...          77.000000     77.000000     77.000000     77.000000   

              SILsv     RmBrdFASv    EducFinaSv    OthrFinaSv          Race  \
count  66972.000000  66972.000000  66972.000000  66972.000000  66972.000000   
mean      18.701398     18.721167     18.773338     18.803425     11.020426   
std       32.956046     32.953075     32.924173     32.915421     28.697648   
min        0.000000      0.000000      0.000000      0.000000      1.000000   
25%        0.000000      0.000000      0.000000      0.000000      1.000000   
50%        0.000000      0.000000      0.000000      0.000000      2.000000   
75%        1.000000      1.000000      1.000000      1.000000      2.000000   
max       77.000000     77.000000     77.000000     77.000000     99.000000   

           RaceEthn  
count  66972.000000  
mean       6.434600  
std       18.517889  
min        1.000000  
25%        1.000000  
50%        2.000000  
75%        6.000000  
max       99.000000  

[8 rows x 30 columns]

In [156]:
# Now I need to review the remaining repeated IDs, and determine which data row I should keep. 
# I will keep the data row that has the larger sum of number of services recieved for the unique ID.

# Function to obtain total number of services:

def check_for_true(data_row):
    
    services = ['TribeSv','DelinqntSv', 'SpecEdSv', 'ILNAsv', 'AcSuppSv', \
            'PSEdSuppSv', 'CareerSv', 'EmplyTrSv', 'BudgetSv', 'HousEdSv', 'HlthEdSv', \
            'FamSuppSv', 'MentorSv', 'SILsv', 'RmBrdFASv', 'EducFinaSv', 'OthrFinaSv']

    services_tally = 0

    for serv in services:
        for value in serv:
#         = cohort_1_reviewDups[serv].value
            print value
#         if value == 1:
#             services_tally += 1
                
#     return services_tally
    


In [ ]:
cohort_1_reviewDups = cohort_1_dups[cohort_1_dups['duplicated_4_sure'] == False]

# cohort_1_reviewDups['TotNum_Serv'] = 
cohort_1_reviewDups.apply(check_for_true, axis=1)

# cohort_1_reviewDups

T
r
i
b
e
S
v
D
e
l
i
n
q
n
t
S
v
S
p
e
c
E
d
S
v
I
L
N
A
s
v
A
c
S
u
p
p
S
v
P
S
E
d
S
u
p
p
S
v
C
a
r
e
e
r
S
v
E
m
p
l
y
T
r
S
v
B
u
d
g
e
t
S
v
H
o
u
s
E
d
S
v
H
l
t
h
E
d
S
v
F
a
m
S
u
p
p
S
v
M
e
n
t
o
r
S
v
S
I
L
s
v
R
m
B
r
d
F
A
S
v
E
d
u
c
F
i
n
a
S
v
O
t
h
r
F
i
n
a
S
v
T
r
i
b
e
S
v
D
e
l
i
n
q
n
t
S
v
S
p
e
c
E
d
S
v
I
L
N
A
s
v
A
c
S
u
p
p
S
v
P
S
E
d
S
u
p
p
S
v
C
a
r
e
e
r
S
v
E
m
p
l
y
T
r
S
v
B
u
d
g
e
t
S
v
H
o
u
s
E
d
S
v
H
l
t
h
E
d
S
v
F
a
m
S
u
p
p
S
v
M
e
n
t
o
r
S
v
S
I
L
s
v
R
m
B
r
d
F
A
S
v
E
d
u
c
F
i
n
a
S
v
O
t
h
r
F
i
n
a
S
v
T
r
i
b
e
S
v
D
e
l
i
n
q
n
t
S
v
S
p
e
c
E
d
S
v
I
L
N
A
s
v
A
c
S
u
p
p
S
v
P
S
E
d
S
u
p
p
S
v
C
a
r
e
e
r
S
v
E
m
p
l
y
T
r
S
v
B
u
d
g
e
t
S
v
H
o
u
s
E
d
S
v
H
l
t
h
E
d
S
v
F
a
m
S
u
p
p
S
v
M
e
n
t
o
r
S
v
S
I
L
s
v
R
m
B
r
d
F
A
S
v
E
d
u
c
F
i
n
a
S
v
O
t
h
r
F
i
n
a
S
v
T
r
i
b
e
S
v
D
e
l
i
n
q
n
t
S
v
S
p
e
c
E
d
S
v
I
L
N
A
s
v
A
c
S
u
p
p
S
v
P
S
E
d
S
u
p
p
S
v
C
a
r
e
e
r
S
v
E
m
p
l
y
T
r
S
v
B
u
d
g
e
t
S
v
H
o
u


In [142]:
services = ['FCStatSv', 'TribeSv','DelinqntSv', 'EdLevlSv', 'SpecEdSv', 'ILNAsv', 'AcSuppSv', \
            'PSEdSuppSv', 'CareerSv', 'EmplyTrSv', 'BudgetSv', 'HousEdSv', 'HlthEdSv', \
            'FamSuppSv', 'MentorSv', 'SILsv', 'RmBrdFASv', 'EducFinaSv', 'OthrFinaSv']

for serv in services:
    print cohort_1_reviewDups[serv].value_counts()

1    68496
0    25106
Name: FCStatSv, dtype: int64
0     84514
77     4648
1      4440
Name: TribeSv, dtype: int64
0     75666
1     13299
77     4637
Name: DelinqntSv, dtype: int64
11    17443
12    15222
10    15077
9     11390
14     6099
8      6092
77     4596
7      2102
13     1853
12     1839
11     1780
10     1674
9      1656
0      1627
77     1595
8       950
6       862
14      611
7       441
13      305
6       226
0       161
          1
Name: EdLevlSv, dtype: int64
0     70259
1     18517
77     4826
Name: SpecEdSv, dtype: int64
0     53407
1     35590
77     4605
Name: ILNAsv, dtype: int64
0     49324
1     39647
77     4631
Name: AcSuppSv, dtype: int64
0     66083
1     22888
77     4631
Name: PSEdSuppSv, dtype: int64
0     54070
1     34900
77     4632
Name: CareerSv, dtype: int64
0     71133
1     17837
77     4632
Name: EmplyTrSv, dtype: int64
0     57690
1     31286
77     4626
Name: BudgetSv, dtype: int64
0     55490
1     33485
77     4627
Name: HousEdSv, dtype

In [127]:
dups_pivot = pd.pivot_table(cohort_1_dups, columns='StFCID')
dups_pivot

StFCID     AK450266294765 AK450290395006 AK450448396586 AK450461296715  \
AcSuppSv              0.5              0              0            0.5   
AmIAKN                  1              0              1              0   
Asian                   0              0              0              0   
BlkAfrAm                0              0              0              0   
BudgetSv                0              0              0              0   
CareerSv                0              0              0              0   
DelinqntSv              0              0              0              0   
EducFinaSv            0.5              0              0              0   
EmplyTrSv               0              0              0              0   
FCStatSv                1              1              1              1   
FY                   2011           2011           2011           2011   
FamSuppSv               0              0              0              0   
HawaiiPI                0              0              0              0   
HisOrgin                0              0              0              0   
HlthEdSv                0              0              0              0   
HousEdSv                1            0.5              0              1   
ILNAsv                  1              0              1              1   
MentorSv                0              0              0              0   
OthrFinaSv              1              1            0.5            0.5   
PSEdSuppSv              0              0              0              0   
Race                    3              1              3              1   
RaceEthn                3              1              3              1   
RepDate            201106         201106         201106         201106   
RmBrdFASv             0.5              0              0              0   
SILsv                   0              0              0              0   
Sex                     1              2              2              2   
SpecEdSv                0           38.5           38.5           38.5   
StFIPS                  2              2              2              2   
TribeSv                 1              0              1              0   
White                   0              1              0              1   
duplicated           True           True           True           True   

StFCID     AK450540097503 AK450571197814 AK450637398476 AK450671998822  \
AcSuppSv                0              0              0              0   
AmIAKN                  0              1              0              1   
Asian                   0              0              0              0   
BlkAfrAm                0              0              0              0   
BudgetSv                0              0              0              0   
CareerSv                0              0              0              0   
DelinqntSv              0            0.5              0              0   
EducFinaSv            0.5              0              0              0   
EmplyTrSv               0              0              0              0   
FCStatSv                1              1              1              1   
FY                   2011           2011           2011           2011   
FamSuppSv               0              0              0              0   
HawaiiPI                0              0              0              0   
HisOrgin                0              0              0              3   
HlthEdSv                0              0              0              0   
HousEdSv              0.5              1              1              0   
ILNAsv                  1              1              1              1   
MentorSv                0              0              0              0   
OthrFinaSv              1            0.5            0.5            0.5   
PSEdSuppSv              0              0              0              0   
Race                    1              3              1              3   
Rac

In [111]:
secCheck = cohort_1_dups.drop(['RepDate'], axis=1)
secCheck.head()

FY  StFIPS  St         DOB  Sex  AmIAKN  Asian  BlkAfrAm  HawaiiPI  \
502461  2011       2  AK   1/15/1993    1       1      0         0         0   
502462  2011       2  AK  10/15/1993    2       0      0         0         0   
502463  2011       2  AK  12/15/1993    2       1      0         0         0   
502464  2011       2  AK  10/15/1993    2       0      0         0         0   
502465  2011       2  AK  10/15/1993    2       0      0         0         0   

        White     ...     MentorSv SILsv  RmBrdFASv  EducFinaSv  OthrFinaSv  \
502461      0     ...            0     0          1           1           1   
502462      1     ...            0     0          0           0           1   
502463      0     ...            0     0          0           0           0   
502464      1     ...            0     0          0           0           1   
502465      1     ...            0     0          0           1           1   

                StFCID Race  RaceEthn  AgeMP  duplicated  
502461  AK450266294765    3         3     18        True  
502462  AK450290395006    1         1     17        True  
502463  AK450448396586    3         3     17        True  
502464  AK450461296715    1         1     17        True  
502465  AK450540097503    1         1     17        True  

[5 rows x 37 columns]

In [120]:
cohort_1_dups.to_csv("cohort_1_dups.csv")

In [112]:
dup_DF = secCheck.duplicated(keep=False)
dupDFDF = secCheck.duplicated(keep='first')

In [113]:
dup_DF.describe()

count     118822
unique         2
top        False
freq      105942
dtype: object

In [114]:
dupDFDF.describe()

count     118822
unique         2
top        False
freq      112382
dtype: object

In [118]:
dup_check_dict2 = dict(dupDFDF)

dup_count3 = pd.DataFrame.from_dict(dup_check_dict2, orient='index')
dup_count3[0].value_counts()

False    112382
True       6440
Name: 0, dtype: int64

In [116]:
dup_count3

0
524288  False
524289  False
524290  False
524292  False
524293  False
524294  False
524295  False
524296  False
524298  False
524299  False
524305  False
524306  False
524309  False
524310  False
524313  False
524314  False
524316  False
524317  False
524322  False
524323  False
524324  False
524328  False
524329  False
524332  False
524333  False
524334  False
524336  False
524341  False
524345  False
524346  False
...       ...
524233  False
524234  False
524236  False
524238  False
524239  False
524241  False
524243  False
524244  False
524245  False
524246  False
524247  False
524248  False
524249  False
524252  False
524253  False
524254  False
524255  False
524257  False
524259  False
524260  False
524261  False
524268  False
524271  False
524272  False
524273  False
524276  False
524278  False
524282  False
524283  False
524284  False

[118822 rows x 1 columns]

In [19]:
outcomes_2013.Wave.value_counts()

Wave 1: Age 17 Baseline Survey    28635
Wave 2: Age 19 Followup           15235
Name: Wave, dtype: int64

In [21]:
outcomes_2014.wave.value_counts()

Age 17 Baseline Survey    23775
Name: wave, dtype: int64

In [10]:


# For now, I only want to examine data for foster youth who are in both W1 and W2

cohort_1.rename(columns={'RepDate':'RepDate_services'}, inplace=True)

outcomes_2013_keep = outcomes_2013.drop(['StFIPS','St','RecNumbr','dob','Sex','AmIAKN','Asian','BlkAfrAm',\
                                         'HawaiiPI','White','RaceUnkn','RaceDcln','HisOrgin'], axis=1)

outcomes_2013_keep.rename(columns={'RepDate':'RepDate_outcomes', 'StChID': 'StFCID'}, inplace=True)

cohort_1 = pd.merge(outcomes_2013_keep, cohort_1, on='StFCID', how='inner')

In [11]:
# Issue with encoding the tracking ID (StFIPS). Need to drop states that have the issue: HI, IN, KY, MS, OR, TX, TN
# bad_encode_states = ["HI", "IN", "KY", "MS", "OR", "TX", "TN"]
cohort_1 = cohort_1[cohort_1.St != "HI"]
cohort_1 = cohort_1[cohort_1.St != "IN"]
cohort_1 = cohort_1[cohort_1.St != "KY"]
cohort_1 = cohort_1[cohort_1.St != "MS"]
cohort_1 = cohort_1[cohort_1.St != "OR"]
cohort_1 = cohort_1[cohort_1.St != "TX"]
cohort_1 = cohort_1[cohort_1.St != "TN"]

dict(cohort_1.StFCID.value_counts())

{'VA269626272263': 4,
 'SC000617715839': 4,
 'AZ008000184681': 2,
 'OHGBOSK46DTHR9': 1,
 'NY260114088260': 2,
 'SC000837155133': 4,
 'MO207576976709': 2,
 'KS0A0A0B1C8G9H': 2,
 'AZ005000546394': 1,
 'DC223329222229': 1,
 'SC000787935532': 4,
 'CA00FlVV71l52F': 2,
 'CA00IF2F3Ce6nO': 2,
 'LAXXXCZSPSIGHX': 2,
 'KS0A0A0A7C1I2J': 2,
 'UT000027083094': 2,
 'WISMOVO0M6JE70': 4,
 'CA00KP2f7pp42A': 2,
 'IAN7ZNY0YHLQMS': 2,
 'CA00JZjVB8F5Us': 1,
 'RI860946899999': 2,
 'NE338049924444': 1,
 'IAN7ZNYM8NE400': 4,
 'WISMOVO4S8DN08': 1,
 'AZ006000590577': 2,
 'WA002D3MPW03G6': 2,
 'KS0A0A0B1E5I6F': 4,
 'CA00B7zKCbi196': 2,
 'CA00KcAibHl3Oi': 2,
 'NY242134966130': 2,
 'CA005zDCeud4md': 1,
 'CA00OJAhn397QN': 2,
 'NC979953338516': 2,
 'NY240646360130': 1,
 'WISMOVOD1UZZ4E': 2,
 'MD100458939149': 2,
 'CA00Eg0xb9u192': 2,
 'FL600004529801': 1,
 'NY240841928010': 2,
 'NY240938469200': 4,
 'CA00Hr2HSiI192': 2,
 'FL142502046101': 1,
 'WISMOVO0M6JE7I': 4,
 'CO000221813118': 2,
 'FL186771010179': 1,
 'GA007400

In [12]:
cohort_1.describe()

/Users/cguy/anaconda/lib/python2.7/site-packages/numpy/lib/function_base.py:3823: RuntimeWarning: Invalid value encountered in percentile
  RuntimeWarning)


Weight       FY  RepDate_services        StFIPS           Sex  \
count  19339.000000  34220.0      34220.000000  34220.000000  34220.000000   
mean       2.584101   2011.0     201106.250731     24.739509      1.508299   
std        2.483794      0.0          2.989548     17.243140      0.499938   
min        0.700000   2011.0     201103.000000      1.000000      1.000000   
25%             NaN   2011.0     201103.000000      6.000000      1.000000   
50%             NaN   2011.0     201109.000000     22.000000      2.000000   
75%             NaN   2011.0     201109.000000     36.000000      2.000000   
max       80.710000   2011.0     201109.000000     72.000000      2.000000   

             AmIAKN         Asian      BlkAfrAm      HawaiiPI         White  \
count  34220.000000  34220.000000  34220.000000  34220.000000  34220.000000   
mean       0.036645      0.014757      0.346084      0.005202      0.545617   
std        0.187892      0.120582      0.475727      0.071936      0.497922   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.000000      0.000000      0.000000      0.000000   
50%        0.000000      0.000000      0.000000      0.000000      1.000000   
75%        0.000000      0.000000      1.000000      0.000000      1.000000   
max        1.000000      1.000000      1.000000      1.000000      1.000000   

           ...           HousEdSv      HlthEdSv     FamSuppSv      MentorSv  \
count      ...       34220.000000  34220.000000  34220.000000  34220.000000   
mean       ...           9.377323      9.390094      9.329018      9.230362   
std        ...          24.704123     24.699530     24.721429     24.756442   
min        ...           0.000000      0.000000      0.000000      0.000000   
25%        ...           0.000000      0.000000      0.000000      0.000000   
50%        ...           0.000000      0.000000      0.000000      0.000000   
75%        ...           1.000000      1.000000      1.000000      1.000000   
max        ...          77.000000     77.000000     77.000000     77.000000   

              SILsv     RmBrdFASv    EducFinaSv    OthrFinaSv          Race  \
count  34220.000000  34220.000000  34220.000000  34220.000000  34220.000000   
mean       9.126008      9.129456      9.157598      9.212858     11.043688   
std       24.792996     24.791796     24.781983     24.762608     28.712294   
min        0.000000      0.000000      0.000000      0.000000      1.000000   
25%        0.000000      0.000000      0.000000      0.000000      1.000000   
50%        0.000000      0.000000      0.000000      0.000000      1.000000   
75%        0.000000      0.000000      0.000000      1.000000      2.000000   
max       77.000000     77.000000     77.000000     77.000000     99.000000   

           RaceEthn  
count  34220.000000  
mean       4.829193  
std       13.945162  
min        1.000000  
25%        1.000000  
50%        2.000000  
75%        6.000000  
max       99.000000  

[8 rows x 31 columns]

In [13]:
# Need to figure out how to treat missing values....

dict(cohort_1.isnull().sum())

{'AcSuppSv': 0,
 'AgeMP': 0,
 'AmIAKN': 0,
 'Asian': 0,
 'Baseline': 0,
 'BlkAfrAm': 0,
 'BudgetSv': 0,
 'CareerSv': 0,
 'Children': 154,
 'CnctAdult': 154,
 'CurrFTE': 154,
 'CurrPTE': 154,
 'CurrenRoll': 154,
 'DOB': 0,
 'DelinqntSv': 0,
 'EdLevlSv': 0,
 'EducAid': 154,
 'EducFinaSv': 0,
 'Elig19': 0,
 'EmplySklls': 154,
 'EmplyTrSv': 0,
 'FCStatSv': 0,
 'FY': 0,
 'FY11Cohort': 0,
 'FamSuppSv': 0,
 'HawaiiPI': 0,
 'HighEdCert': 200,
 'HisOrgin': 0,
 'HlthEdSv': 0,
 'Homeless': 154,
 'HousEdSv': 0,
 'ILNAsv': 0,
 'InSample': 18613,
 'Incarc': 154,
 'Marriage': 154,
 'Medicaid': 154,
 'MedicalIn': 154,
 'MentlHlthIn': 154,
 'MentorSv': 0,
 'OthrFinAs': 154,
 'OthrFinaSv': 0,
 'OthrHlthIn': 154,
 'OutcmDte': 4135,
 'OutcmFCS': 154,
 'OutcmRpt': 154,
 'PSEdSuppSv': 0,
 'PrescripIn': 154,
 'PubFinAs': 154,
 'PubFoodAs': 154,
 'PubHousAs': 157,
 'Race': 0,
 'RaceDcln': 0,
 'RaceEthn': 0,
 'RaceUnkn': 0,
 'RepDate_outcomes': 0,
 'RepDate_services': 0,
 'Responded': 0,
 'RmBrdFASv': 0,
 'SIL

In [14]:
# For now, I am dropping rows that have NaNs in 10+ columns....

cohort_1 = cohort_1[cohort_1.HighEdCert.notnull()]
cohort_1 = cohort_1[cohort_1.PubHousAs.notnull()]

In [15]:
dict(cohort_1.isnull().sum())

{'AcSuppSv': 0,
 'AgeMP': 0,
 'AmIAKN': 0,
 'Asian': 0,
 'Baseline': 0,
 'BlkAfrAm': 0,
 'BudgetSv': 0,
 'CareerSv': 0,
 'Children': 0,
 'CnctAdult': 0,
 'CurrFTE': 0,
 'CurrPTE': 0,
 'CurrenRoll': 0,
 'DOB': 0,
 'DelinqntSv': 0,
 'EdLevlSv': 0,
 'EducAid': 0,
 'EducFinaSv': 0,
 'Elig19': 0,
 'EmplySklls': 0,
 'EmplyTrSv': 0,
 'FCStatSv': 0,
 'FY': 0,
 'FY11Cohort': 0,
 'FamSuppSv': 0,
 'HawaiiPI': 0,
 'HighEdCert': 0,
 'HisOrgin': 0,
 'HlthEdSv': 0,
 'Homeless': 0,
 'HousEdSv': 0,
 'ILNAsv': 0,
 'InSample': 18569,
 'Incarc': 0,
 'Marriage': 0,
 'Medicaid': 0,
 'MedicalIn': 0,
 'MentlHlthIn': 0,
 'MentorSv': 0,
 'OthrFinAs': 0,
 'OthrFinaSv': 0,
 'OthrHlthIn': 0,
 'OutcmDte': 4135,
 'OutcmFCS': 0,
 'OutcmRpt': 0,
 'PSEdSuppSv': 0,
 'PrescripIn': 0,
 'PubFinAs': 0,
 'PubFoodAs': 0,
 'PubHousAs': 0,
 'Race': 0,
 'RaceDcln': 0,
 'RaceEthn': 0,
 'RaceUnkn': 0,
 'RepDate_outcomes': 0,
 'RepDate_services': 0,
 'Responded': 0,
 'RmBrdFASv': 0,
 'SILsv': 0,
 'SampleState': 0,
 'Sex': 0,
 'SocS

In [16]:
dict(cohort_1.dtypes)

{'AcSuppSv': dtype('int64'),
 'AgeMP': dtype('O'),
 'AmIAKN': dtype('int64'),
 'Asian': dtype('int64'),
 'Baseline': dtype('O'),
 'BlkAfrAm': dtype('int64'),
 'BudgetSv': dtype('int64'),
 'CareerSv': dtype('int64'),
 'Children': dtype('O'),
 'CnctAdult': dtype('O'),
 'CurrFTE': dtype('O'),
 'CurrPTE': dtype('O'),
 'CurrenRoll': dtype('O'),
 'DOB': dtype('O'),
 'DelinqntSv': dtype('int64'),
 'EdLevlSv': dtype('O'),
 'EducAid': dtype('O'),
 'EducFinaSv': dtype('int64'),
 'Elig19': dtype('O'),
 'EmplySklls': dtype('O'),
 'EmplyTrSv': dtype('int64'),
 'FCStatSv': dtype('int64'),
 'FY': dtype('int64'),
 'FY11Cohort': dtype('O'),
 'FamSuppSv': dtype('int64'),
 'HawaiiPI': dtype('int64'),
 'HighEdCert': dtype('O'),
 'HisOrgin': dtype('int64'),
 'HlthEdSv': dtype('int64'),
 'Homeless': dtype('O'),
 'HousEdSv': dtype('int64'),
 'ILNAsv': dtype('int64'),
 'InSample': dtype('O'),
 'Incarc': dtype('O'),
 'Marriage': dtype('O'),
 'Medicaid': dtype('O'),
 'MedicalIn': dtype('O'),
 'MentlHlthIn': dty

In [17]:
#Need to convert AgeMP, EduLevlSv to int

cohort_1['AgeMP'] = cohort_1['AgeMP'].apply(lambda x: int(x))
cohort_1['EdLevlSv'] = cohort_1['EdLevlSv'].apply(lambda x: int(x))

In [18]:
# Fix mixed types in RaceDcl, RaceUnkn (need to be type int):

def treat_blank_strings(row_with_string):
    """Find blank strings ("") and convert to value 77 (which represents blank in raw data codebook). 
    Also, convert all values to type int."""
    if type(row_with_string) == int:
        return row_with_string
    elif row_with_string == "0":
        return 0
    elif row_with_string == "1":
        return 1
    else:
        return 77

In [19]:
print cohort_1.RaceDcln.value_counts()
cohort_1['RaceDcln'] = cohort_1['RaceDcln'].apply(treat_blank_strings)
cohort_1.RaceDcln.value_counts()

0    16187
0    11466
      4026
1     1245
1     1093
Name: RaceDcln, dtype: int64


0     27653
77     4026
1      2338
Name: RaceDcln, dtype: int64

In [20]:
print cohort_1.RaceUnkn.value_counts()
cohort_1['RaceUnkn'] = cohort_1['RaceUnkn'].apply(treat_blank_strings)
cohort_1.RaceUnkn.value_counts()

0    30034
0     3022
       484
1      441
1       36
Name: RaceUnkn, dtype: int64


0     33056
77      484
1       477
Name: RaceUnkn, dtype: int64

In [21]:
#Need to convert RepDates and DOBs to datetime

cohort_1.RepDate_services = pd.to_datetime(cohort_1['RepDate_services'], format="%Y%m")
cohort_1.DOB = pd.to_datetime(cohort_1['DOB'])

In [22]:
# Need to address blanks in RepDates_outcomes column before converting to datetime....

print cohort_1.RepDate_outcomes.value_counts()

def treat_blank_dates(row_with_string):
    """Find blank dates ("") and convert to value 199901 (I need to decide what to do with blanks later)."""
    if len(row_with_string) == 0:
        return int("199901")
    else:
        return row_with_string

cohort_1['RepDate_outcomes'] = cohort_1['RepDate_outcomes'].apply(treat_blank_dates)
print cohort_1.RepDate_outcomes.value_counts()
cohort_1.RepDate_outcomes = pd.to_datetime(cohort_1['RepDate_outcomes'], format="%Y%m")

201103    11517
201109    10248
201309     5689
201303     5674
            543
201203      346
Name: RepDate_outcomes, dtype: int64
201103    11517
201109    10248
201309     5689
201303     5674
199901      543
201203      346
Name: RepDate_outcomes, dtype: int64


In [23]:
dict(cohort_1.dtypes)

{'AcSuppSv': dtype('int64'),
 'AgeMP': dtype('int64'),
 'AmIAKN': dtype('int64'),
 'Asian': dtype('int64'),
 'Baseline': dtype('O'),
 'BlkAfrAm': dtype('int64'),
 'BudgetSv': dtype('int64'),
 'CareerSv': dtype('int64'),
 'Children': dtype('O'),
 'CnctAdult': dtype('O'),
 'CurrFTE': dtype('O'),
 'CurrPTE': dtype('O'),
 'CurrenRoll': dtype('O'),
 'DOB': dtype('<M8[ns]'),
 'DelinqntSv': dtype('int64'),
 'EdLevlSv': dtype('int64'),
 'EducAid': dtype('O'),
 'EducFinaSv': dtype('int64'),
 'Elig19': dtype('O'),
 'EmplySklls': dtype('O'),
 'EmplyTrSv': dtype('int64'),
 'FCStatSv': dtype('int64'),
 'FY': dtype('int64'),
 'FY11Cohort': dtype('O'),
 'FamSuppSv': dtype('int64'),
 'HawaiiPI': dtype('int64'),
 'HighEdCert': dtype('O'),
 'HisOrgin': dtype('int64'),
 'HlthEdSv': dtype('int64'),
 'Homeless': dtype('O'),
 'HousEdSv': dtype('int64'),
 'ILNAsv': dtype('int64'),
 'InSample': dtype('O'),
 'Incarc': dtype('O'),
 'Marriage': dtype('O'),
 'Medicaid': dtype('O'),
 'MedicalIn': dtype('O'),
 'Men

In [24]:
# Depending on tyoe of modeling techniques I will use, 
# I will need to turn the following into numeric categories: 

# wave, OutcmRpt, OutcmFCS, CurrFTE, CurrPTE, EmplySkills, SocSecrty,
# 'EducAid','PubFinAs','PubFoodAs','PubHousAs','OthrFinAs','HighEdCert','CurrenRoll','CnctAdult',
# 'Marriage','Medicaid','OthrHlthIn','MedicalIn','MentlHlthIn','PrescripIn','Baseline','FY11Cohort',
# 'Elig19','SampleState','InSample','Responded'

In [25]:
# Need to fix encoding in column HighEdCert

cohort_1.HighEdCert.value_counts()

None of the above          15041
Blank                      13142
High school diploma/GED     4699
Declined                     734
78.0                         201
Vocational certificate       132
Vocational license            35
Higher degree                 17
Associate�s degree            10
Bachelor�s degree              6
Name: HighEdCert, dtype: int64

In [26]:
def change_weird_chars(row):
    if type(row) == str:
        if 'Bachelor' in row:
            return "Bachelor's Degree"
        elif 'Associate' in row:
            return "Associate's Degree"
        else:
            return row
    
cohort_1.HighEdCert = cohort_1['HighEdCert'].apply(change_weird_chars)

cohort_1.HighEdCert.value_counts()

None of the above          15041
Blank                      13142
High school diploma/GED     4699
Declined                     734
Vocational certificate       132
Vocational license            35
Higher degree                 17
Associate's Degree            10
Bachelor's Degree              6
Name: HighEdCert, dtype: int64

In [27]:
cohort_1.head()

Wave          StFCID RepDate_outcomes  \
0  Wave 1: Age 17 Baseline Survey  AK450290395006       2011-03-01   
1  Wave 1: Age 17 Baseline Survey  AK450290395006       2011-03-01   
2         Wave 2: Age 19 Followup  AK450290395006       2013-03-01   
3         Wave 2: Age 19 Followup  AK450290395006       2013-03-01   
4  Wave 1: Age 17 Baseline Survey  AK450448396586       2011-03-01   

             OutcmRpt   OutcmDte                  OutcmFCS CurrFTE CurrPTE  \
0  Youth participated 2010-10-08     Yes, is in FC on Date      No      No   
1  Youth participated 2010-10-08     Yes, is in FC on Date      No      No   
2  Youth participated 2012-12-28  No, is not in FC on Date      No      No   
3  Youth participated 2012-12-28  No, is not in FC on Date      No      No   
4  Youth participated 2010-12-28     Yes, is in FC on Date      No      No   

  EmplySklls                               SocSecrty  ...  HlthEdSv FamSuppSv  \
0         No  Yes, is receiving SSI or SSDI payments  ...         0         0   
1         No  Yes, is receiving SSI or SSDI payments  ...         0         0   
2         No                                      No  ...         0         0   
3         No                                      No  ...         0         0   
4        Yes                                      No  ...         0         0   

  MentorSv SILsv RmBrdFASv EducFinaSv OthrFinaSv Race RaceEthn AgeMP  
0        0     0         0          0          1    1        1    17  
1        0     0         0          0          1    1        1    17  
2        0     0         0          0          1    1        1    17  
3        0     0         0          0          1    1        1    17  
4        0     0         0          0          0    3        3    17  

[5 rows x 71 columns]

In [28]:
cohort_1.describe()

Weight       FY        StFIPS           Sex        AmIAKN  \
count  19298.000000  34017.0  34017.000000  34017.000000  34017.000000   
mean       2.586975   2011.0     24.546756      1.508099      0.036658   
std        2.485643      0.0     16.992185      0.499942      0.187924   
min        0.700000   2011.0      1.000000      1.000000      0.000000   
25%             NaN   2011.0      6.000000      1.000000      0.000000   
50%             NaN   2011.0     22.000000      2.000000      0.000000   
75%             NaN   2011.0     36.000000      2.000000      0.000000   
max       80.710000   2011.0     72.000000      2.000000      1.000000   

              Asian      BlkAfrAm      HawaiiPI         White      RaceUnkn  \
count  34017.000000  34017.000000  34017.000000  34017.000000  34017.000000   
mean       0.014846      0.347473      0.005174      0.545198      1.109592   
std        0.120936      0.476175      0.071744      0.497960      9.118341   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.000000      0.000000      0.000000      0.000000   
50%        0.000000      0.000000      0.000000      1.000000      0.000000   
75%        0.000000      1.000000      0.000000      1.000000      0.000000   
max        1.000000      1.000000      1.000000      1.000000     77.000000   

           ...           HlthEdSv     FamSuppSv      MentorSv         SILsv  \
count      ...       34017.000000  34017.000000  34017.000000  34017.000000   
mean       ...           9.441926      9.380663      9.284652      9.178617   
std        ...          24.763954     24.785990     24.820182     24.857457   
min        ...           0.000000      0.000000      0.000000      0.000000   
25%        ...           0.000000      0.000000      0.000000      0.000000   
50%        ...           0.000000      0.000000      0.000000      0.000000   
75%        ...           1.000000      1.000000      1.000000      0.000000   
max        ...          77.000000     77.000000     77.000000     77.000000   

          RmBrdFASv    EducFinaSv    OthrFinaSv          Race      RaceEthn  \
count  34017.000000  34017.000000  34017.000000  34017.000000  34017.000000   
mean       9.182703      9.210542      9.265985     10.954934      4.819620   
std       24.856030     24.846288     24.826781     28.588251     13.976082   
min        0.000000      0.000000      0.000000      1.000000      1.000000   
25%        0.000000      0.000000      0.000000      1.000000      1.000000   
50%        0.000000      0.000000      0.000000      1.000000      2.000000   
75%        0.000000      0.000000      1.000000      2.000000      6.000000   
max       77.000000     77.000000     77.000000     99.000000     99.000000   

              AgeMP  
count  34017.000000  
mean      16.543552  
std        0.519542  
min       14.000000  
25%       16.000000  
50%       17.000000  
75%       17.000000  
max       20.000000  

[8 rows x 34 columns]

In [29]:
# Now that I have dataset for cohort_1 in a decent state, I will load this into a local postgres DB for storage

In [30]:
engine = create_engine('postgresql://cguy@localhost:5432/nytd_clean_data')
cohort_1.to_sql('cohort_1', engine)

In [31]:
%load_ext sql
# %reload_ext sql

/Users/cguy/anaconda/lib/python2.7/site-packages/IPython/config.py:13: ShimWarning: The `IPython.config` package has been deprecated. You should import from traitlets.config instead.
  "You should import from traitlets.config instead.", ShimWarning)
/Users/cguy/anaconda/lib/python2.7/site-packages/IPython/utils/traitlets.py:5: UserWarning: IPython.utils.traitlets has moved to a top-level traitlets package.
  warn("IPython.utils.traitlets has moved to a top-level traitlets package.")


In [32]:
%%sql postgresql://cguy@localhost:5432/nytd_clean_data
        
SELECT * FROM cohort_1 LIMIT 5;

5 rows affected.


[(0L, u'Wave 1: Age 17 Baseline Survey', u'AK450290395006', datetime.datetime(2011, 3, 1, 0, 0), u'Youth participated', datetime.datetime(2010, 10, 8, 0, 0), u'Yes, is in FC on Date', u'No', u'No', u'No', u'Yes, is receiving SSI or SSDI payments', u'No', u'No', u'No', u'No', u'No', u'None of the above', u'Yes', u'Yes', u'No', u'Yes', u'No', u'No', u'No', u'Yes', u'No', u"Don't Know", u'Yes', u'Yes', u'No', None, u'Yes', u'Yes', u'Yes', 1.26, u'Responded to Survey', 2011L, datetime.datetime(2011, 9, 1, 0, 0), 2L, u'AK', datetime.datetime(1993, 10, 15, 0, 0), 2L, 0L, 0L, 0L, 0L, 1L, 0L, 0L, 0L, 1L, 0L, 0L, 11L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 1L, 0L, 0L, 0L, 0L, 0L, 0L, 1L, 1L, 1L, 17L),
 (1L, u'Wave 1: Age 17 Baseline Survey', u'AK450290395006', datetime.datetime(2011, 3, 1, 0, 0), u'Youth participated', datetime.datetime(2010, 10, 8, 0, 0), u'Yes, is in FC on Date', u'No', u'No', u'No', u'Yes, is receiving SSI or SSDI payments', u'No', u'No', u'No', u'No', u'No', u'None of the above', u'Yes', u'Yes', u'No', u'Yes', u'No', u'No', u'No', u'Yes', u'No', u"Don't Know", u'Yes', u'Yes', u'No', None, u'Yes', u'Yes', u'Yes', 1.26, u'Responded to Survey', 2011L, datetime.datetime(2011, 3, 1, 0, 0), 2L, u'AK', datetime.datetime(1993, 10, 15, 0, 0), 2L, 0L, 0L, 0L, 0L, 1L, 0L, 0L, 0L, 1L, 0L, 0L, 77L, 77L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 1L, 1L, 1L, 17L),
 (2L, u'Wave 2: Age 19 Followup', u'AK450290395006', datetime.datetime(2013, 3, 1, 0, 0), u'Youth participated', datetime.datetime(2012, 12, 28, 0, 0), u'No, is not in FC on Date', u'No', u'No', u'No', u'No', u'No', u'No', u'Yes', u'No', u'No', u'None of the above', u'No', u'Yes', u'Yes', u'No', u'No', u'No', u'Not Applicable', u'Yes', u'No', u'Not Applicable', u'Not Applicable', u'Not Applicable', u'No', u'No', u'Yes', u'Yes', u'Yes', 1.58, u'Responded to Survey', 2011L, datetime.datetime(2011, 9, 1, 0, 0), 2L, u'AK', datetime.datetime(1993, 10, 15, 0, 0), 2L, 0L, 0L, 0L, 0L, 1L, 0L, 0L, 0L, 1L, 0L, 0L, 11L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 1L, 0L, 0L, 0L, 0L, 0L, 0L, 1L, 1L, 1L, 17L),
 (3L, u'Wave 2: Age 19 Followup', u'AK450290395006', datetime.datetime(2013, 3, 1, 0, 0), u'Youth participated', datetime.datetime(2012, 12, 28, 0, 0), u'No, is not in FC on Date', u'No', u'No', u'No', u'No', u'No', u'No', u'Yes', u'No', u'No', u'None of the above', u'No', u'Yes', u'Yes', u'No', u'No', u'No', u'Not Applicable', u'Yes', u'No', u'Not Applicable', u'Not Applicable', u'Not Applicable', u'No', u'No', u'Yes', u'Yes', u'Yes', 1.58, u'Responded to Survey', 2011L, datetime.datetime(2011, 3, 1, 0, 0), 2L, u'AK', datetime.datetime(1993, 10, 15, 0, 0), 2L, 0L, 0L, 0L, 0L, 1L, 0L, 0L, 0L, 1L, 0L, 0L, 77L, 77L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 1L, 1L, 1L, 17L),
 (4L, u'Wave 1: Age 17 Baseline Survey', u'AK450448396586', datetime.datetime(2011, 3, 1, 0, 0), u'Youth participated', datetime.datetime(2010, 12, 28, 0, 0), u'Yes, is in FC on Date', u'No', u'No', u'Yes', u'No', u'No', u'Yes', u'Yes', u'Yes', u'No', u'None of the above', u'Yes', u'Yes', u'No', u'No', u'No', u'No', u'Not Applicable', u'No', u'No', u'No', u'No', u'No', u'No', None, u'Yes', u'Yes', u'Yes', 1.36, u'Responded to Survey', 2011L, datetime.datetime(2011, 9, 1, 0, 0), 2L, u'AK', datetime.datetime(1993, 12, 15, 0, 0), 2L, 1L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 1L, 1L, 0L, 11L, 0L, 1L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 0L, 3L, 3L, 17L)]

# Now Cohort 2

In [33]:
# For cohort 2, only need services data for FY 2014

cohort_2 = services_11_14[services_11_14.FY == 2014]
cohort_2 = cohort_2.drop(['RecNumbr','LclFIPSsv'],axis= 1)

# For now, I only want to examine data for foster youth who are in W1

cohort_2.rename(columns={'RepDate':'RepDate_services'}, inplace=True)

outcomes_2014_keep = outcomes_2014.drop(['stfips','st','recnumbr','dob','sex','amiakn','asian','blkafram',\
                                         'hawaiipi','white','raceunkn','racedcln','hisorgin','race','raceethn'], axis=1)

outcomes_2014_keep.rename(columns={'repdate':'RepDate_outcomes', 'stfcid': 'StFCID'}, inplace=True)

cohort_2 = pd.merge(outcomes_2014_keep, cohort_2, on='StFCID', how='inner')

In [34]:
# Issue with encoding the tracking ID (StFIPS). Need to drop states that have the issue: HI, IN, KY, MS, OR, TX, TN
# bad_encode_states = ["HI", "IN", "KY", "MS", "OR", "TX", "TN"]
cohort_2 = cohort_2[cohort_2.St != "HI"]
cohort_2 = cohort_2[cohort_2.St != "IN"]
cohort_2 = cohort_2[cohort_2.St != "KY"]
cohort_2 = cohort_2[cohort_2.St != "MS"]
cohort_2 = cohort_2[cohort_2.St != "OR"]
cohort_2 = cohort_2[cohort_2.St != "TX"]
cohort_2 = cohort_2[cohort_2.St != "TN"]

dict(cohort_2.StFCID.value_counts())

{'MD100450694537': 1,
 'KS0A0A0B2G2E1I': 1,
 'IAN7ZNYMPIW4LH': 1,
 'CA003pCp0Fx4wm': 1,
 'NY241689189020': 2,
 'CA0080UqO7JAhd': 2,
 'CA00ICZpZY37S9': 2,
 'WA002D3PXD55JI': 2,
 'LAXXXCZZIGXCAA': 2,
 'AZ003000931714': 1,
 'CA005VFguhO196': 2,
 'CA002mA9a8PC06': 2,
 'CA004i6FjUG7XZ': 1,
 'NY241624566030': 2,
 'CA00HuyN4GsDR5': 2,
 'IL000067021290': 1,
 'OK005922257221': 1,
 'NC979948199989': 1,
 'IAN7ZNY0YKB4CH': 2,
 'PAYKC6DLQHUERG': 2,
 'UT000029414495': 1,
 'CA005b5aFDm5mf': 2,
 'NE305134024444': 2,
 'NY251184704180': 2,
 'LAXXXCZGZCAZAS': 2,
 'NV200000203058': 1,
 'MI000044261489': 1,
 'CA004O8s9EF5EE': 2,
 'CA00OfoQ30k4tA': 2,
 'FL310007596201': 2,
 'LAXXXCZZPSHZSH': 2,
 'KS0A0A0B2G9G6H': 1,
 'MO204573099316': 1,
 'PAJKCTML8KVNRG': 2,
 'MD100458295199': 1,
 'WISMOVO4ZQ5WH8': 1,
 'PAYKIVMLQAU6RG': 1,
 'VA214720242201': 2,
 'OHGB7SKN6TFHP9': 2,
 'MO923567227702': 2,
 'LAXXXCZZSAHGGC': 2,
 'NY241733632050': 2,
 'PAYKY08LQJU6RG': 1,
 'CA00U2tCu97AS2': 2,
 'MD100458238645': 1,
 'IAN7ZNY0

In [35]:
cohort_2.describe()

responded       FY  RepDate_services        StFIPS           Sex  \
count  18253.000000  18253.0      18253.000000  18253.000000  18253.000000   
mean       0.781680   2014.0     201406.193448     23.266203      1.505122   
std        0.413117      0.0          2.993839     16.358002      0.499987   
min        0.000000   2014.0     201403.000000      1.000000      1.000000   
25%        1.000000   2014.0     201403.000000      6.000000      1.000000   
50%        1.000000   2014.0     201409.000000     20.000000      2.000000   
75%        1.000000   2014.0     201409.000000     36.000000      2.000000   
max        1.000000   2014.0     201409.000000     72.000000      2.000000   

             AmIAKN         Asian      BlkAfrAm      HawaiiPI         White  \
count  18253.000000  18253.000000  18253.000000  18253.000000  18253.000000   
mean       0.047828      0.025201      0.362023      0.014409      0.560894   
std        0.828726      0.815973      0.933927      0.809597      0.942099   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.000000      0.000000      0.000000      0.000000   
50%        0.000000      0.000000      0.000000      0.000000      1.000000   
75%        0.000000      0.000000      1.000000      0.000000      1.000000   
max       77.000000     77.000000     77.000000     77.000000     77.000000   

           ...           HousEdSv      HlthEdSv     FamSuppSv      MentorSv  \
count      ...       18253.000000  18253.000000  18253.000000  18253.000000   
mean       ...           0.382458      0.395168      0.311620      0.231688   
std        ...           1.469670      1.470632      1.462279      1.449742   
min        ...           0.000000      0.000000      0.000000      0.000000   
25%        ...           0.000000      0.000000      0.000000      0.000000   
50%        ...           0.000000      0.000000      0.000000      0.000000   
75%        ...           1.000000      1.000000      1.000000      0.000000   
max        ...          77.000000     77.000000     77.000000     77.000000   

              SILsv     RmBrdFASv    EducFinaSv    OthrFinaSv          Race  \
count  18253.000000  18253.000000  18253.000000  18253.000000  18253.000000   
mean       0.082562      0.103052      0.133622      0.246699     11.610146   
std        0.629581      1.419919      1.428113      1.452440     29.305791   
min        0.000000      0.000000      0.000000      0.000000      1.000000   
25%        0.000000      0.000000      0.000000      0.000000      1.000000   
50%        0.000000      0.000000      0.000000      0.000000      2.000000   
75%        0.000000      0.000000      0.000000      0.000000      2.000000   
max       77.000000     77.000000     77.000000     77.000000     99.000000   

           RaceEthn  
count  18253.000000  
mean       3.912781  
std        9.303250  
min        1.000000  
25%        1.000000  
50%        2.000000  
75%        6.000000  
max       99.000000  

[8 rows x 31 columns]

In [36]:
# No NaNs....

dict(cohort_2.isnull().sum())

{'AcSuppSv': 0,
 'AgeMP': 0,
 'AmIAKN': 0,
 'Asian': 0,
 'BlkAfrAm': 0,
 'BudgetSv': 0,
 'CareerSv': 0,
 'DOB': 0,
 'DelinqntSv': 0,
 'EdLevlSv': 0,
 'EducFinaSv': 0,
 'EmplyTrSv': 0,
 'FCStatSv': 0,
 'FY': 0,
 'FamSuppSv': 0,
 'HawaiiPI': 0,
 'HisOrgin': 0,
 'HlthEdSv': 0,
 'HousEdSv': 0,
 'ILNAsv': 0,
 'MentorSv': 0,
 'OthrFinaSv': 0,
 'PSEdSuppSv': 0,
 'Race': 0,
 'RaceDcln': 0,
 'RaceEthn': 0,
 'RaceUnkn': 0,
 'RepDate_outcomes': 0,
 'RepDate_services': 0,
 'RmBrdFASv': 0,
 'SILsv': 0,
 'Sex': 0,
 'SpecEdSv': 0,
 'St': 0,
 'StFCID': 0,
 'StFIPS': 0,
 'TribeSv': 0,
 'White': 0,
 'baseline': 0,
 'children': 0,
 'cnctadult': 0,
 'currenroll': 0,
 'currfte': 0,
 'currpte': 0,
 'educaid': 0,
 'elig19': 0,
 'emplysklls': 0,
 'fy14cohort': 0,
 'highedcert': 0,
 'homeless': 0,
 'incarc': 0,
 'insample': 0,
 'marriage': 0,
 'medicaid': 0,
 'medicalin': 0,
 'mentlhlthin': 0,
 'othrfinas': 0,
 'othrhlthin': 0,
 'outcmdte': 0,
 'outcmfcs': 0,
 'outcmrpt': 0,
 'prescripin': 0,
 'pubfinas': 0,
 

In [37]:
dict(cohort_2.dtypes)

{'AcSuppSv': dtype('int64'),
 'AgeMP': dtype('O'),
 'AmIAKN': dtype('int64'),
 'Asian': dtype('int64'),
 'BlkAfrAm': dtype('int64'),
 'BudgetSv': dtype('int64'),
 'CareerSv': dtype('int64'),
 'DOB': dtype('O'),
 'DelinqntSv': dtype('int64'),
 'EdLevlSv': dtype('O'),
 'EducFinaSv': dtype('int64'),
 'EmplyTrSv': dtype('int64'),
 'FCStatSv': dtype('int64'),
 'FY': dtype('int64'),
 'FamSuppSv': dtype('int64'),
 'HawaiiPI': dtype('int64'),
 'HisOrgin': dtype('int64'),
 'HlthEdSv': dtype('int64'),
 'HousEdSv': dtype('int64'),
 'ILNAsv': dtype('int64'),
 'MentorSv': dtype('int64'),
 'OthrFinaSv': dtype('int64'),
 'PSEdSuppSv': dtype('int64'),
 'Race': dtype('int64'),
 'RaceDcln': dtype('O'),
 'RaceEthn': dtype('int64'),
 'RaceUnkn': dtype('O'),
 'RepDate_outcomes': dtype('O'),
 'RepDate_services': dtype('int64'),
 'RmBrdFASv': dtype('int64'),
 'SILsv': dtype('int64'),
 'Sex': dtype('int64'),
 'SpecEdSv': dtype('int64'),
 'St': dtype('O'),
 'StFCID': dtype('O'),
 'StFIPS': dtype('int64'),
 'Tr

In [38]:
#Need to convert AgeMP, EduLevlSv, RaceDcln, RaceUnkn to int

cohort_2['AgeMP'] = cohort_2['AgeMP'].apply(lambda x: int(x))
cohort_2['EdLevlSv'] = cohort_2['EdLevlSv'].apply(lambda x: int(x))
cohort_2['RaceDcln'] = cohort_2['RaceDcln'].apply(lambda x: int(x))
cohort_2['RaceUnkn'] = cohort_2['RaceUnkn'].apply(lambda x: int(x))


In [39]:
#Need to convert columns RepDates, DOB, and outcmdte to datetime

cohort_2['DOB'] = cohort_2['DOB'].apply(lambda x: x.zfill(10))

cohort_2.RepDate_outcomes = pd.to_datetime(cohort_2['RepDate_outcomes'], format="%Y%m")
cohort_2.RepDate_services = pd.to_datetime(cohort_2['RepDate_services'], format="%Y%m")
cohort_2.DOB = pd.to_datetime(cohort_2['DOB'])

In [40]:
cohort_2.DOB.value_counts()

1996-12-15    1792
1996-10-15    1682
1997-01-15    1640
1996-11-15    1634
1997-05-15    1557
1997-07-15    1495
1997-02-15    1490
1997-03-15    1472
1997-06-15    1412
1997-04-15    1388
1997-08-15    1353
1997-09-15    1332
1994-02-15       1
1996-08-15       1
1996-06-15       1
1997-10-15       1
1996-01-15       1
1992-08-15       1
Name: DOB, dtype: int64

In [41]:
# Need to address blanks in outcmdte column before converting to datetime....

print cohort_2.outcmdte.value_counts()

def treat_blank_dates2(row_with_string):
    """Find blank dates ("") and convert to value 01/01/1999 (I need to decide what to do with blanks later)."""
    if len(row_with_string) <= 3 :
        return "01/01/1999"
    else:
        return row_with_string

cohort_2['outcmdte'] = cohort_2['outcmdte'].apply(treat_blank_dates2)

print cohort_2.outcmdte.value_counts()

cohort_2.outcmdte = pd.to_datetime(cohort_2['outcmdte'], format="%m/%d/%Y")

              1323
1/22/2014      113
1/7/2014       113
3/24/2014      103
3/26/2014      102
3/31/2014      100
9/23/2014       98
1/14/2014       97
9/30/2014       97
11/14/2013      97
7/31/2014       95
3/25/2014       89
2/11/2014       89
1/2/2014        88
7/16/2014       88
7/2/2014        86
12/11/2013      86
9/24/2014       85
12/17/2013      85
1/29/2014       84
5/29/2014       84
4/23/2014       83
3/20/2014       83
8/6/2014        83
2/26/2014       82
8/19/2014       82
1/10/2014       81
1/9/2014        80
7/30/2014       80
11/27/2013      79
              ... 
4/12/2014        5
6/22/2014        4
10/2/2013        4
11/9/2013        4
10/27/2013       4
10/26/2014       4
10/25/2014       4
11/2/2014        4
8/24/2014        4
8/31/2014        4
8/23/2014        4
11/11/2014       4
11/5/2014        4
10/1/2013        4
10/19/2014       4
5/31/2014        3
11/1/2014        3
11/10/2014       3
11/18/2014       2
11/9/2014        2
3/1/2015         2
1/13/2013   

In [42]:
dict(cohort_2.dtypes)

{'AcSuppSv': dtype('int64'),
 'AgeMP': dtype('int64'),
 'AmIAKN': dtype('int64'),
 'Asian': dtype('int64'),
 'BlkAfrAm': dtype('int64'),
 'BudgetSv': dtype('int64'),
 'CareerSv': dtype('int64'),
 'DOB': dtype('<M8[ns]'),
 'DelinqntSv': dtype('int64'),
 'EdLevlSv': dtype('int64'),
 'EducFinaSv': dtype('int64'),
 'EmplyTrSv': dtype('int64'),
 'FCStatSv': dtype('int64'),
 'FY': dtype('int64'),
 'FamSuppSv': dtype('int64'),
 'HawaiiPI': dtype('int64'),
 'HisOrgin': dtype('int64'),
 'HlthEdSv': dtype('int64'),
 'HousEdSv': dtype('int64'),
 'ILNAsv': dtype('int64'),
 'MentorSv': dtype('int64'),
 'OthrFinaSv': dtype('int64'),
 'PSEdSuppSv': dtype('int64'),
 'Race': dtype('int64'),
 'RaceDcln': dtype('int64'),
 'RaceEthn': dtype('int64'),
 'RaceUnkn': dtype('int64'),
 'RepDate_outcomes': dtype('<M8[ns]'),
 'RepDate_services': dtype('<M8[ns]'),
 'RmBrdFASv': dtype('int64'),
 'SILsv': dtype('int64'),
 'Sex': dtype('int64'),
 'SpecEdSv': dtype('int64'),
 'St': dtype('O'),
 'StFCID': dtype('O'),
 

In [43]:
# Depending on tyoe of modeling techniques I will use, 
# I will need to turn the following into numeric categories: 

# wave, OutcmRpt, OutcmFCS, CurrFTE, CurrPTE, EmplySkills, SocSecrty,
# 'EducAid','PubFinAs','PubFoodAs','PubHousAs','OthrFinAs','HighEdCert','CurrenRoll','CnctAdult',
# 'Marriage','Medicaid','OthrHlthIn','MedicalIn','MentlHlthIn','PrescripIn','Baseline','FY11Cohort',
# 'Elig19','SampleState','InSample','Responded'

In [44]:
cohort_2.head()

wave RepDate_outcomes      outcmrpt   outcmdte outcmfcs  \
0  Age 17 Baseline Survey       2014-09-01  participated 2014-05-14      yes   
1  Age 17 Baseline Survey       2014-09-01      declined 1999-01-01      yes   
2  Age 17 Baseline Survey       2014-09-01  participated 2014-06-26      yes   
3  Age 17 Baseline Survey       2014-09-01  participated 2014-09-29      yes   
4  Age 17 Baseline Survey       2014-09-01      declined 1999-01-01      yes   

  currfte currpte emplysklls socsecrty educaid  ...  HlthEdSv FamSuppSv  \
0      no     yes         no        no      no  ...         1         1   
1   blank   blank      blank     blank   blank  ...         1         1   
2      no      no         no        no      no  ...         1         1   
3      no      no         no        no      no  ...         1         0   
4   blank   blank      blank     blank   blank  ...         1         1   

  MentorSv SILsv RmBrdFASv EducFinaSv OthrFinaSv Race RaceEthn AgeMP  
0        1     0         0          0          0    2        2    16  
1        1     0         0          0          0    1        1    16  
2        1     0         0          0          0    1        7    16  
3        0     1         0          0          0    1        1    16  
4        1     0         0          0          0    1        1    16  

[5 rows x 70 columns]

In [45]:
cohort_2.describe()

responded       FY        StFIPS           Sex        AmIAKN  \
count  18253.000000  18253.0  18253.000000  18253.000000  18253.000000   
mean       0.781680   2014.0     23.266203      1.505122      0.047828   
std        0.413117      0.0     16.358002      0.499987      0.828726   
min        0.000000   2014.0      1.000000      1.000000      0.000000   
25%        1.000000   2014.0      6.000000      1.000000      0.000000   
50%        1.000000   2014.0     20.000000      2.000000      0.000000   
75%        1.000000   2014.0     36.000000      2.000000      0.000000   
max        1.000000   2014.0     72.000000      2.000000     77.000000   

              Asian      BlkAfrAm      HawaiiPI         White      RaceUnkn  \
count  18253.000000  18253.000000  18253.000000  18253.000000  18253.000000   
mean       0.025201      0.362023      0.014409      0.560894      0.026023   
std        0.815973      0.933927      0.809597      0.942099      0.816451   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.000000      0.000000      0.000000      0.000000   
50%        0.000000      0.000000      0.000000      1.000000      0.000000   
75%        0.000000      1.000000      0.000000      1.000000      0.000000   
max       77.000000     77.000000     77.000000     77.000000     77.000000   

           ...           HlthEdSv     FamSuppSv      MentorSv         SILsv  \
count      ...       18253.000000  18253.000000  18253.000000  18253.000000   
mean       ...           0.395168      0.311620      0.231688      0.082562   
std        ...           1.470632      1.462279      1.449742      0.629581   
min        ...           0.000000      0.000000      0.000000      0.000000   
25%        ...           0.000000      0.000000      0.000000      0.000000   
50%        ...           0.000000      0.000000      0.000000      0.000000   
75%        ...           1.000000      1.000000      0.000000      0.000000   
max        ...          77.000000     77.000000     77.000000     77.000000   

          RmBrdFASv    EducFinaSv    OthrFinaSv          Race      RaceEthn  \
count  18253.000000  18253.000000  18253.000000  18253.000000  18253.000000   
mean       0.103052      0.133622      0.246699     11.610146      3.912781   
std        1.419919      1.428113      1.452440     29.305791      9.303250   
min        0.000000      0.000000      0.000000      1.000000      1.000000   
25%        0.000000      0.000000      0.000000      1.000000      1.000000   
50%        0.000000      0.000000      0.000000      2.000000      2.000000   
75%        0.000000      0.000000      0.000000      2.000000      6.000000   
max       77.000000     77.000000     77.000000     99.000000     99.000000   

              AgeMP  
count  18253.000000  
mean      16.545992  
std        0.499322  
min       16.000000  
25%       16.000000  
50%       17.000000  
75%       17.000000  
max       21.000000  

[8 rows x 34 columns]

In [46]:
# Now that I have dataset for cohort_1 in a decent state, I will load this into a local postgres DB for storage

In [47]:
cohort_2.to_sql('cohort_2', engine)

In [48]:
%%sql postgresql://cguy@localhost:5432/nytd_clean_data
        
SELECT * FROM cohort_2 LIMIT 5;

5 rows affected.


[(0L, u'Age 17 Baseline Survey', datetime.datetime(2014, 9, 1, 0, 0), u'participated', datetime.datetime(2014, 5, 14, 0, 0), u'yes', u'no', u'yes', u'no', u'no', u'no', u'no', u'no', u'no', u'no', u'none of the above', u'yes', u'yes', u'no', u'no', u'no', u'no', u'not applicable', u'yes', u'no', u'not applicable', u'not applicable', u'not applicable', u'yes', u'yes', u'yes', u'no', u'Not a Sample State', 1L, u'AL000000227321', 2014L, datetime.datetime(2014, 3, 1, 0, 0), 1L, u'AL', datetime.datetime(1997, 4, 15, 0, 0), 1L, 0L, 0L, 1L, 0L, 0L, 0L, 0L, 0L, 1L, 0L, 0L, 9L, 0L, 0L, 1L, 1L, 1L, 1L, 1L, 1L, 1L, 1L, 1L, 0L, 0L, 0L, 0L, 2L, 2L, 16L),
 (1L, u'Age 17 Baseline Survey', datetime.datetime(2014, 9, 1, 0, 0), u'declined', datetime.datetime(1999, 1, 1, 0, 0), u'yes', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'yes', u'no', u'no', u'no', u'Not a Sample State', 0L, u'AL000003716611', 2014L, datetime.datetime(2014, 3, 1, 0, 0), 1L, u'AL', datetime.datetime(1997, 4, 15, 0, 0), 1L, 0L, 0L, 0L, 0L, 1L, 0L, 0L, 0L, 1L, 0L, 0L, 0L, 0L, 0L, 1L, 0L, 0L, 0L, 1L, 1L, 1L, 1L, 1L, 0L, 0L, 0L, 0L, 1L, 1L, 16L),
 (2L, u'Age 17 Baseline Survey', datetime.datetime(2014, 9, 1, 0, 0), u'participated', datetime.datetime(2014, 6, 26, 0, 0), u'yes', u'no', u'no', u'no', u'no', u'no', u'no', u'no', u'no', u'no', u'none of the above', u'yes', u'yes', u'no', u'yes', u'no', u'no', u'not applicable', u'yes', u'no', u'not applicable', u'not applicable', u'not applicable', u'yes', u'yes', u'yes', u'no', u'Not a Sample State', 1L, u'AL000008395721', 2014L, datetime.datetime(2014, 3, 1, 0, 0), 1L, u'AL', datetime.datetime(1997, 5, 15, 0, 0), 1L, 0L, 0L, 0L, 0L, 1L, 0L, 0L, 1L, 1L, 0L, 0L, 10L, 0L, 1L, 1L, 1L, 1L, 0L, 1L, 1L, 1L, 1L, 1L, 0L, 0L, 0L, 0L, 1L, 7L, 16L),
 (3L, u'Age 17 Baseline Survey', datetime.datetime(2014, 9, 1, 0, 0), u'participated', datetime.datetime(2014, 9, 29, 0, 0), u'yes', u'no', u'no', u'no', u'no', u'no', u'no', u'no', u'no', u'no', u'none of the above', u'yes', u'yes', u'no', u'yes', u'no', u'no', u'not applicable', u'yes', u'no', u'not applicable', u'not applicable', u'not applicable', u'yes', u'yes', u'yes', u'no', u'Not a Sample State', 1L, u'AL000026713423', 2014L, datetime.datetime(2014, 3, 1, 0, 0), 1L, u'AL', datetime.datetime(1997, 9, 15, 0, 0), 2L, 0L, 0L, 0L, 0L, 1L, 0L, 0L, 2L, 1L, 0L, 0L, 7L, 0L, 0L, 1L, 0L, 0L, 0L, 1L, 0L, 1L, 0L, 0L, 1L, 0L, 0L, 0L, 1L, 1L, 16L),
 (4L, u'Age 17 Baseline Survey', datetime.datetime(2014, 9, 1, 0, 0), u'declined', datetime.datetime(1999, 1, 1, 0, 0), u'yes', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'blank', u'yes', u'no', u'no', u'no', u'Not a Sample State', 0L, u'AL000030924123', 2014L, datetime.datetime(2014, 3, 1, 0, 0), 1L, u'AL', datetime.datetime(1997, 5, 15, 0, 0), 2L, 0L, 0L, 0L, 0L, 1L, 0L, 0L, 0L, 1L, 0L, 0L, 10L, 1L, 0L, 1L, 0L, 1L, 0L, 1L, 1L, 1L, 1L, 1L, 0L, 0L, 0L, 0L, 1L, 1L, 16L)]